In [1]:
import os
import sys
import math
import random
import numpy as np
import cv2
import json
import matplotlib
import matplotlib.pyplot as plt
import tensorflow as tf
import warnings

warnings.filterwarnings('ignore')

# Root directory of the project
ROOT_DIR = os.getcwd()

from mrcnn.config import Config
from mrcnn import model as modellib,utils
from mrcnn import visualize
from mrcnn.model import log
from PIL import Image

# Directory to save logs and trained model
MODEL_DIR = os.path.join(ROOT_DIR,"logs")

iter_num = 0

# Local path to trained weights file
COCO_MODEL_PATH = os.path.join(ROOT_DIR,"mask_rcnn_coco.h5")
if not os.path.exists(COCO_MODEL_PATH):
    utils.download_trained_weights(COCO_MODEL_PATH)

Using TensorFlow backend.


In [2]:
class ShapesConfig(Config):
    """Configuration for training on the toy shapes dataset.
    Derives from the base Config class and overrides values specific
    to the toy shapes dataset.
    """
    # Give the configuration a recognizable name
    NAME = "shapes"

    # Train on 1 GPU and 8 images per GPU. We can put multiple images on each
    # GPU because the images are small. Batch size is 8 (GPUs * images/GPU).
    GPU_COUNT = 1
    IMAGES_PER_GPU = 2

    # Number of classes (including background)
    NUM_CLASSES = 1 + 3  # background +  shapes

    # Use small images for faster training. Set the limits of the small side
    # the large side, and that determines the image shape.
    IMAGE_MIN_DIM = 320 # 128
    IMAGE_MAX_DIM = 384 #128

    # Use smaller anchors because our image and objects are small
    RPN_ANCHOR_SCALES = (8 *6, 16*6, 32*6, 64*6, 128*6)  # anchor side in pixels

    # Reduce training ROIs per image because the images are small and have
    # few objects. Aim to allow ROI sampling to pick 33% positive ROIs.
    TRAIN_ROIS_PER_IMAGE = 32

    # Use a small epoch since the data is simple
    STEPS_PER_EPOCH = 100

    # use small validation steps since the epoch is small
    VALIDATION_STEPS = 25
    
config = ShapesConfig()
config.display()



Configurations:
BACKBONE                       resnet101
BACKBONE_STRIDES               [4, 8, 16, 32, 64]
BATCH_SIZE                     2
BBOX_STD_DEV                   [0.1 0.1 0.2 0.2]
COMPUTE_BACKBONE_SHAPE         None
DETECTION_MAX_INSTANCES        100
DETECTION_MIN_CONFIDENCE       0.7
DETECTION_NMS_THRESHOLD        0.3
FPN_CLASSIF_FC_LAYERS_SIZE     1024
GPU_COUNT                      1
GRADIENT_CLIP_NORM             5.0
IMAGES_PER_GPU                 2
IMAGE_CHANNEL_COUNT            3
IMAGE_MAX_DIM                  384
IMAGE_META_SIZE                16
IMAGE_MIN_DIM                  320
IMAGE_MIN_SCALE                0
IMAGE_RESIZE_MODE              square
IMAGE_SHAPE                    [384 384   3]
LEARNING_MOMENTUM              0.9
LEARNING_RATE                  0.001
LOSS_WEIGHTS                   {'rpn_class_loss': 1.0, 'rpn_bbox_loss': 1.0, 'mrcnn_class_loss': 1.0, 'mrcnn_bbox_loss': 1.0, 'mrcnn_mask_loss': 1.0}
MASK_POOL_SIZE                 14
MASK_SHAPE             

In [3]:
def get_ax(rows=1, cols=1, size=8):
    """Return a Matplotlib Axes array to be used in
    all visualizations in the notebook. Provide a
    central point to control graph sizes.
    
    Change the default size attribute to control the size
    of rendered images
    """
    _, ax = plt.subplots(rows, cols, figsize=(size*cols, size*rows))
    return ax


In [27]:
class BlockDataset(utils.Dataset):
    # get the instances of th image
    def get_obj_index(self,image):
        n = np.max(image)
        return n
    
    # read json.file to get labels and mask              
    def get_class(self, image_id):
        '''
        info = self.image_info[image_id]
        with open("all_labels.json") as f:
            temp = json.load(f)
            labels = temp[info]['regions'][1]['region_attributes']['label']
        '''
        file = open('mask_index.txt','r')
        all_labels = file.readlines()
        labels = all_labels[int(image_id)]
        
        return labels
    
    # draw_mask
    def draw_mask(self,num_obj,mask,image,image_id):
        info = self.image_info[image_id]
        for index in range(num_obj):
            for i in range(info['width']):
                for j in range(info['height']):
                    at_pixel = image.getpixel((i,j))
                    if at_pixel == index + 1:
                        mask[j,i,index] = 1
        return mask
    
    def load_shapes(self,count,img_folder,mask_folder,imglist,dataset_root_path):
        # Add classes
       
        self.add_class("shapes",1,"large")
        self.add_class("shapes",2,"medium")
        self.add_class("shapes",3,"small")
        
        # "red_s","red_m","red_l","yellow_s","yellow_m","yellow_l","green_s",
        # "green_m","green_l","blue_s","blue_m","blue_l","orange_s","orange_m","orange_l"
        '''
        self.add_class("shapes",1,"red_s")
        self.add_class("shapes",2,"res_m")
        self.add_class("shapes",3,"red_l")
        self.add_class("shapes",4,"yellow_s")
        self.add_class("shapes",5,"yellow_m")
        self.add_class("shapes",6,"yellow_l")
        self.add_class("shapes",7,"green_s")
        self.add_class("shapes",8,"green_m")
        self.add_class("shapes",9,"green_l")
        self.add_class("shapes",10,"blue_s")
        self.add_class("shapes",11,"blue_m")
        self.add_class("shapes",12,"blue_l")
        self.add_class("shapes",13,"orange_s")
        self.add_class("shapes",14,"orange_m")
        self.add_class("shapes",15,"orange_l")
        '''
        
        for i in range(count):
            filestr = imglist[i].split(".")[0]
            # print(filestr)
            mask_path = mask_folder +"/image%s_mask.png" % filestr
            # mask_path = mask_folder +"/" + filestr + ".png"
            # yaml_path = dataset_root_path + "labelme_json/"+filestr+"_json/info.yaml"
            path2Img = img_folder+ "/%s.png" % filestr
            cv_img = cv2.imread(path2Img)
            image_id = filestr
            self.add_image("shapes",image_id = image_id, path = path2Img,
                            width = cv_img.shape[1],height = cv_img.shape[0],mask_path = mask_path)
    '''
    def load_image(self, image_id):
        info = self.image_info[image_id]
        img = np.array(cv2.imread(info['path'],dtype=np.uint8)
                       
        return img
    '''
    
    def load_mask(self,image_id):
        global iter_num
        info = self.image_info[image_id]
        img = Image.open(info['mask_path']) 
        labels = []
        labels = self.get_class(image_id)
        num_obj = len(labels)
        mask = np.zeros([info['height'],info['width'],num_obj], dtype = np.uint8)
        mask = self.draw_mask(num_obj,mask,img,image_id)
        occlusion = np.logical_not(mask[:,:,-1]).astype(np.uint8)
        for i in range(num_obj-2,-1,-1):
            mask[:,:,i] *= occlusion
            occlusion = np.logical_and(occlusion,np.logical_not(mask[:,:,i]))
        labels_form = []
        for i in range(len(labels)):
            if labels[i].find("l") != -1:
                labels.form.append("large")
            elif labels[i].find("m") != -1:
                labels.form.append("medium")
            else:
                labels.form.append("small")
        class_ids = np.array([self.class_names.index(s) for s in labels_form])
        return mask,class_ids.astype(np.int32)

In [28]:
# initialization
dataset_root_path = "train/"
img_folder = dataset_root_path + "pics"
mask_folder = dataset_root_path + "Masks"
imglist = os.listdir(img_folder)
count = len(imglist)

# traning data and validation data
dataset_train = BlockDataset()
dataset_train.load_shapes(count,img_folder,mask_folder,imglist,dataset_root_path)
dataset_train.prepare()
print("dataset_train-->",dataset_train._image_ids)
print('-----',dataset_train.get_class(dataset_train.image_ids[1]))

val_dataset_root_path = "val/"
val_img_folder = val_dataset_root_path + "pics"
val_mask_folder = val_dataset_root_path + "Masks"
val_imglist = os.listdir(val_img_folder)

dataset_val = BlockDataset()
dataset_val.load_shapes(4,val_img_folder,val_mask_folder,val_imglist,val_dataset_root_path)
dataset_val.prepare()
print("dataset_val-->",dataset_val._image_ids)


dataset_train--> [ 0  1  2  3  4  5  6  7  8  9 10 11 12 13 14]
----- [[u'green_s', u'yellow_s', u'yellow_m', u'red_m', u'blue_s']]

dataset_val--> [0 1 2 3]


In [29]:
# Load and display random samples
'''
'''
image_ids = np.random.choice(dataset_train.image_ids,2)
mask,class_ids = dataset_train.load_mask(3)
print(class_ids)
'''
for image_id in image_ids:
    image = dataset_train.load_image(image_id)
    mask,class_ids = dataset_train.load_mask(image_id)
    visualize.display_top_masks(image,mask,class_ids,dataset_train.class_names)
'''



ok
good
very good
prety
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


...

come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on
come on


KeyboardInterrupt: 